# 🚗 **Section 1: Data Import and Initial Processing for Parking Analysis**

## 📥 Step 1: Bring in Libraries & Read the Data File

In [43]:
import numpy as np
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt

In [44]:
# Read the dataset into a DataFrame
df = pd.read_csv('dataset.csv')

In [45]:
# Step 1B: Merge date and time columns into a single timestamp
df['Timestamp'] = pd.to_datetime(
    df['LastUpdatedDate'] + ' ' + df['LastUpdatedTime'],
    dayfirst=True
)

In [46]:
# Preview the dataset to understand its structure
df.head()

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy VehicleType  \
0   0      BHMBCCMKT01       577  26.144536  91.736172         61         car   
1   1      BHMBCCMKT01       577  26.144536  91.736172         64         car   
2   2      BHMBCCMKT01       577  26.144536  91.736172         80         car   
3   3      BHMBCCMKT01       577  26.144536  91.736172        107         car   
4   4      BHMBCCMKT01       577  26.144536  91.736172        150        bike   

  TrafficConditionNearby  QueueLength  IsSpecialDay LastUpdatedDate  \
0                    low            1             0      04-10-2016   
1                    low            1             0      04-10-2016   
2                    low            2             0      04-10-2016   
3                    low            2             0      04-10-2016   
4                    low            2             0      04-10-2016   

  LastUpdatedTime           Timestamp  
0        07:59:00 2016-10-04 07:59:00  
1        08:25:00 2016-10-04 08:25:00  
2        08:59:00 2016-10-04 08:59:00  
3        09:32:00 2016-10-04 09:32:00  
4        09:59:00 2016-10-04 09:59:00

# 🧼 **Step 2: Data Cleaning and Feature Engineering**

Data Preprocessing involves the following steps:
1. Transforming categorical variables like **traffic** and **vehicle type** into numerical format.
2. Generating normalized versions of:
   * **Occupancy** (represented as a fraction of total capacity)
   * **Queue length** (scaled to fall between 0 and 1)

## **2A. Transform Categorical Data**

In [47]:
# Convert 'TrafficConditionNearby' to numeric codes
# low → 0, average → 1, high → 2

traffic_mapping = {'low': 0, 'average': 1, 'high': 2}
df['TrafficLevel'] = df['TrafficConditionNearby'].map(traffic_mapping)

In [48]:
# Assign weights to 'VehicleType'
# These weights reflect the relative space or demand

vehicle_weights = {
    'cycle': 0.3,
    'bike': 0.5,
    'car': 1.0,   # reference value
    'truck': 1.5
}
df['VehicleWeight'] = df['VehicleType'].map(vehicle_weights)

In [49]:
# Fill missing or unmapped values

df['TrafficLevel'] = df['TrafficLevel'].fillna(1)     # Use 'average' as default
df['VehicleWeight'] = df['VehicleWeight'].fillna(1.0) # Use 'car' as default

## **2B. Feature Normalization**

In [50]:
# Calculate occupancy as a fraction of capacity

df['OccupancyRate'] = df['Occupancy'] / df['Capacity']

In [51]:
# Scale QueueLength to a 0-1 range

max_queue = df['QueueLength'].max()
df['QueueNorm'] = df['QueueLength'] / max_queue

## **2C. Create Final Feature Set for Modeling**

In [52]:
# This step ensures that our model only uses relevant and clean columns.

# Final cleaned DataFrame for modeling
df_model = df[['SystemCodeNumber', 'Timestamp', 'OccupancyRate', 'QueueNorm',
               'TrafficLevel', 'IsSpecialDay', 'VehicleWeight']]

In [53]:
# Preview the preprocessed data
df_model.head()

SystemCodeNumber           Timestamp  OccupancyRate  QueueNorm  \
0      BHMBCCMKT01 2016-10-04 07:59:00       0.105719   0.066667   
1      BHMBCCMKT01 2016-10-04 08:25:00       0.110919   0.066667   
2      BHMBCCMKT01 2016-10-04 08:59:00       0.138648   0.133333   
3      BHMBCCMKT01 2016-10-04 09:32:00       0.185442   0.133333   
4      BHMBCCMKT01 2016-10-04 09:59:00       0.259965   0.133333   

   TrafficLevel  IsSpecialDay  VehicleWeight  
0             0             0            1.0  
1             0             0            1.0  
2             0             0            1.0  
3             0             0            1.0  
4             0             0            0.5

# Step 3: Model 1 - Baseline Linear Pricing Model

Baseline Linear Pricing Model

This model updates parking prices dynamically based on occupancy rate.  
The price at time *t+1* depends on the price at time *t* and the current occupancy rate.

A simple model where the next price is a function of the previous price and current occupancy:
- Linear price increase as occupancy increases
- Acts as a reference point

**Example:**
Price<sub>t+1</sub> = Price<sub>t</sub> + α × ( Occupancy / Capacity )

In [54]:
# Initialize base price and parameter alpha
base_price = 10
alpha = 5  # controls sensitivity to occupancy rate

In [55]:
# Sort data by timestamp and parking lot for time series logic
df = df.sort_values(by=['SystemCodeNumber', 'Timestamp'])

In [56]:
# Create a new column for price, initialize with base_price
df['Price'] = base_price
df['Price'] = df['Price'].astype(float)  # Convert Price column to float to avoid dtype issues

In [57]:
# Calculate occupancy rate again just to be accurate
df['OccupancyRate'] = df['Occupancy'] / df['Capacity']

In [58]:
# Iterate over each parking lot separately to update prices over time
for lot in df['SystemCodeNumber'].unique():
    lot_data = df[df['SystemCodeNumber'] == lot].copy()

In [59]:
# Update prices sequentially for each timestamp
for i in range(1, len(lot_data)):
        prev_price = lot_data.iloc[i-1]['Price']
        occupancy_rate = lot_data.iloc[i]['OccupancyRate']

In [60]:
# Calculate new price with linear update
new_price = prev_price + alpha * occupancy_rate

In [61]:
# Bound the price to avoid unreasonable jumps (optional)
new_price = max(5, min(new_price, 30))  # price between $5 and $30

In [62]:
# Assign the price back
df.loc[lot_data.index[i], 'Price'] = new_price

In [63]:
# Preview updated prices
df[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'Capacity', 'Price']].head(20)

SystemCodeNumber           Timestamp  Occupancy  Capacity  Price
0       BHMBCCMKT01 2016-10-04 07:59:00         61       577   10.0
1       BHMBCCMKT01 2016-10-04 08:25:00         64       577   10.0
2       BHMBCCMKT01 2016-10-04 08:59:00         80       577   10.0
3       BHMBCCMKT01 2016-10-04 09:32:00        107       577   10.0
4       BHMBCCMKT01 2016-10-04 09:59:00        150       577   10.0
5       BHMBCCMKT01 2016-10-04 10:26:00        177       577   10.0
6       BHMBCCMKT01 2016-10-04 10:59:00        219       577   10.0
7       BHMBCCMKT01 2016-10-04 11:25:00        247       577   10.0
8       BHMBCCMKT01 2016-10-04 11:59:00        259       577   10.0
9       BHMBCCMKT01 2016-10-04 12:29:00        266       577   10.0
10      BHMBCCMKT01 2016-10-04 13:02:00        269       577   10.0
11      BHMBCCMKT01 2016-10-04 13:29:00        263       577   10.0
12      BHMBCCMKT01 2016-10-04 14:02:00        238       577   10.0
13      BHMBCCMKT01 2016-10-04 14:29:00        215       577   10.0
14      BHMBCCMKT01 2016-10-04 14:57:00        192       577   10.0
15      BHMBCCMKT01 2016-10-04 15:30:00        165       577   10.0
16      BHMBCCMKT01 2016-10-04 16:04:00        162       577   10.0
17      BHMBCCMKT01 2016-10-04 16:31:00        143       577   10.0
18      BHMBCCMKT01 2016-10-05 07:57:00         54       577   10.0
19      BHMBCCMKT01 2016-10-05 08:30:00         59       577   10.0

# Step 4: Model 2 – Price Adjustment Using Demand Factors

In [64]:
# Define base price and demand sensitivity parameter
base_price = 10
lambda_ = 0.8  # Controls how strongly demand affects price

In [65]:
# Map categorical traffic conditions to numeric values (higher means worse traffic)
traffic_mapping = {'low': 0.5, 'average': 1.0, 'high': 1.5}
df['TrafficLevel'] = df['TrafficConditionNearby'].map(traffic_mapping).fillna(1.0)

In [66]:
# Map vehicle types to numeric weights representing their impact on demand
vehicle_weights = {'car': 1.0, 'bike': 0.7, 'truck': 1.2, 'cycle': 0.5}
df['VehicleWeight'] = df['VehicleType'].map(vehicle_weights).fillna(1.0)

In [67]:
# Normalize QueueLength by max queue length in dataset to scale between 0 and 1
max_queue = df['QueueLength'].max()
df['QueueNorm'] = df['QueueLength'] / max_queue

In [68]:
# Ensure OccupancyRate is calculated
df['OccupancyRate'] = df['Occupancy'] / df['Capacity']

In [69]:
# Prepare to compute demand score
alpha = 3.0    # weight for occupancy rate
beta = 2.0     # weight for queue length
gamma = 1.5    # weight for traffic congestion (subtracted)
delta = 4.0    # weight for special day effect
epsilon = 1.0  # weight for vehicle type

In [70]:
# Calculate demand score for each record
df['DemandScore'] = (alpha * df['OccupancyRate'] +
                     beta * df['QueueNorm'] -
                     gamma * df['TrafficLevel'] +
                     delta * df['IsSpecialDay'] +
                     epsilon * df['VehicleWeight'])

# Normalize demand scores to 0-1 range for stable price scaling
demand_min = df['DemandScore'].min()
demand_max = df['DemandScore'].max()
df['DemandNorm'] = (df['DemandScore'] - demand_min) / (demand_max - demand_min)

# Initialize Price column with base price
df['Price'] = base_price
df['Price'] = df['Price'].astype(float)

# Iterate over each parking lot to update prices based on demand
for lot in df['SystemCodeNumber'].unique():
    lot_data = df[df['SystemCodeNumber'] == lot].copy()
    
    # For each time step, calculate new price bounded between 0.5x and 2x base price
    for i in range(len(lot_data)):
        demand = lot_data.iloc[i]['DemandNorm']
        new_price = base_price * (1 + lambda_ * demand)
        new_price = max(base_price * 0.5, min(new_price, base_price * 2.0))
        df.loc[lot_data.index[i], 'Price'] = new_price

# Preview first 20 rows with prices updated by demand-based model
df[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'QueueLength', 'TrafficConditionNearby',
    'IsSpecialDay', 'VehicleType', 'Price']].head(20)


SystemCodeNumber           Timestamp  Occupancy  QueueLength  \
0       BHMBCCMKT01 2016-10-04 07:59:00         61            1   
1       BHMBCCMKT01 2016-10-04 08:25:00         64            1   
2       BHMBCCMKT01 2016-10-04 08:59:00         80            2   
3       BHMBCCMKT01 2016-10-04 09:32:00        107            2   
4       BHMBCCMKT01 2016-10-04 09:59:00        150            2   
5       BHMBCCMKT01 2016-10-04 10:26:00        177            3   
6       BHMBCCMKT01 2016-10-04 10:59:00        219            6   
7       BHMBCCMKT01 2016-10-04 11:25:00        247            5   
8       BHMBCCMKT01 2016-10-04 11:59:00        259            5   
9       BHMBCCMKT01 2016-10-04 12:29:00        266            8   
10      BHMBCCMKT01 2016-10-04 13:02:00        269            7   
11      BHMBCCMKT01 2016-10-04 13:29:00        263            7   
12      BHMBCCMKT01 2016-10-04 14:02:00        238            5   
13      BHMBCCMKT01 2016-10-04 14:29:00        215            3   
14      BHMBCCMKT01 2016-10-04 14:57:00        192            3   
15      BHMBCCMKT01 2016-10-04 15:30:00        165            2   
16      BHMBCCMKT01 2016-10-04 16:04:00        162            1   
17      BHMBCCMKT01 2016-10-04 16:31:00        143            2   
18      BHMBCCMKT01 2016-10-05 07:57:00         54            1   
19      BHMBCCMKT01 2016-10-05 08:30:00         59            1   

   TrafficConditionNearby  IsSpecialDay VehicleType      Price  
0                     low             0         car  11.219162  
1                     low             0         car  11.233854  
2                     low             0         car  11.437796  
3                     low             0         car  11.570020  
4                     low             0        bike  11.498031  
5                     low             0         car  12.038412  
6                    high             0       truck  11.396387  
7                 average             0         car  11.925966  
8                 average             0       cycle  11.513784  
9                    high             0        bike  11.406780  
10                   high             0         car  11.578455  
11                   high             0         car  11.549071  
12                   high             0         car  11.175468  
13                average             0       truck  11.706462  
14                average             0        bike  11.122877  
15                    low             0         car  11.854059  
16                    low             0        bike  11.431212  
17                average             0         car  11.039897  
18                    low             0         car  11.184882  
19                average             0         car  10.502944

# Step 5: Model 3 – Competition-Aware Pricing and Smart Rerouting

### Goals:
* Leverage location data to find nearby parking competitors
* Compare and adjust prices based on local competition
* Suggest rerouting if your lot is full and cheaper options are close

### Highlights:
* Use latitude/longitude and Haversine distance
* Identify competitors within a set radius (e.g., 1 km)
* Dynamically compare and adjust prices
* Lower price or suggest rerouting if full and cheaper lots exist
* Raise price if nearby lots are more expensive

In [71]:
# Haversine formula to calculate distance (km) between two lat/lon points
def haversine(lat1, lon1, lat2, lon2):
    R = 6371  # Earth radius in kilometers
    phi1, phi2 = np.radians(lat1), np.radians(lat2)
    delta_phi = np.radians(lat2 - lat1)
    delta_lambda = np.radians(lon2 - lon1)

    a = np.sin(delta_phi/2)**2 + np.cos(phi1)*np.cos(phi2)*np.sin(delta_lambda/2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    return R * c

In [72]:
# Set radius threshold for competitor proximity (e.g., 1 km)
proximity_threshold = 1.0

In [73]:
# Create a DataFrame to store latest prices for each lot for quick lookup
latest_prices = df.groupby('SystemCodeNumber')['Price'].last()

In [74]:
# Function to find nearby competitor lots within radius
def find_nearby_competitors(current_lot):
    lat1 = df.loc[df['SystemCodeNumber'] == current_lot, 'Latitude'].iloc[0]
    lon1 = df.loc[df['SystemCodeNumber'] == current_lot, 'Longitude'].iloc[0]
    
    nearby_lots = []
    for lot in df['SystemCodeNumber'].unique():
        if lot == current_lot:
            continue
        lat2 = df.loc[df['SystemCodeNumber'] == lot, 'Latitude'].iloc[0]
        lon2 = df.loc[df['SystemCodeNumber'] == lot, 'Longitude'].iloc[0]
        distance = haversine(lat1, lon1, lat2, lon2)
        if distance <= proximity_threshold:
            nearby_lots.append(lot)
    return nearby_lots

In [75]:
# Update prices incorporating competitor logic
for lot in df['SystemCodeNumber'].unique():
    lot_indices = df[df['SystemCodeNumber'] == lot].index
    
    nearby_lots = find_nearby_competitors(lot)
    nearby_prices = latest_prices.loc[nearby_lots] if nearby_lots else pd.Series(dtype=float)
    
    for i in lot_indices:
        current_price = df.loc[i, 'Price']
        occupancy = df.loc[i, 'Occupancy']
        capacity = df.loc[i, 'Capacity']
        
        # If lot is full or over 90% occupancy, check competitors
        if occupancy >= 0.9 * capacity and not nearby_prices.empty:
            min_competitor_price = nearby_prices.min()
            if min_competitor_price < current_price:
                # Lower price slightly or suggest rerouting
                new_price = max(5, min_competitor_price * 0.95)  # 5% cheaper than competitor
                df.loc[i, 'Price'] = new_price
                df.loc[i, 'RerouteSuggestion'] = True  # You can add a new column to flag rerouting
            else:
                # Competitors more expensive, can increase price moderately
                new_price = min(30, current_price * 1.05)  # Increase price by 5%
                df.loc[i, 'Price'] = new_price
                df.loc[i, 'RerouteSuggestion'] = False
        else:
            # Normal pricing, no rerouting
            df.loc[i, 'RerouteSuggestion'] = False

In [76]:
# Check updated prices and rerouting suggestions
df[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'Capacity', 'Price', 'RerouteSuggestion']].head(20)

SystemCodeNumber           Timestamp  Occupancy  Capacity      Price  \
0       BHMBCCMKT01 2016-10-04 07:59:00         61       577  11.219162   
1       BHMBCCMKT01 2016-10-04 08:25:00         64       577  11.233854   
2       BHMBCCMKT01 2016-10-04 08:59:00         80       577  11.437796   
3       BHMBCCMKT01 2016-10-04 09:32:00        107       577  11.570020   
4       BHMBCCMKT01 2016-10-04 09:59:00        150       577  11.498031   
5       BHMBCCMKT01 2016-10-04 10:26:00        177       577  12.038412   
6       BHMBCCMKT01 2016-10-04 10:59:00        219       577  11.396387   
7       BHMBCCMKT01 2016-10-04 11:25:00        247       577  11.925966   
8       BHMBCCMKT01 2016-10-04 11:59:00        259       577  11.513784   
9       BHMBCCMKT01 2016-10-04 12:29:00        266       577  11.406780   
10      BHMBCCMKT01 2016-10-04 13:02:00        269       577  11.578455   
11      BHMBCCMKT01 2016-10-04 13:29:00        263       577  11.549071   
12      BHMBCCMKT01 2016-10-04 14:02:00        238       577  11.175468   
13      BHMBCCMKT01 2016-10-04 14:29:00        215       577  11.706462   
14      BHMBCCMKT01 2016-10-04 14:57:00        192       577  11.122877   
15      BHMBCCMKT01 2016-10-04 15:30:00        165       577  11.854059   
16      BHMBCCMKT01 2016-10-04 16:04:00        162       577  11.431212   
17      BHMBCCMKT01 2016-10-04 16:31:00        143       577  11.039897   
18      BHMBCCMKT01 2016-10-05 07:57:00         54       577  11.184882   
19      BHMBCCMKT01 2016-10-05 08:30:00         59       577  10.502944   

   RerouteSuggestion  
0              False  
1              False  
2              False  
3              False  
4              False  
5              False  
6              False  
7              False  
8              False  
9              False  
10             False  
11             False  
12             False  
13             False  
14             False  
15             False  
16             False  
17             False  
18             False  
19             False

* Calculate distances between lots using coordinates
* Find competitors within 1 km (adjustable)
* If your lot is nearly full, check competitor prices
* Lower price and suggest rerouting if cheaper lots are nearby
* Raise price if competitors are pricier
* Otherwise, keep pricing steady

# Step 6: Real-Time Simulation with Pathway – Linear Pricing Model

In [77]:
import pathway
print(pathway.__file__)

c:\Users\user\AppData\Local\Programs\Python\Python313\Lib\site-packages\pathway\__init__.py


In [78]:
BASE_PRICE = 10
ALPHA = 5  # Linear sensitivity

# Prepare result list to hold rows as dictionaries
streamed_rows = []

# Sort data for consistent simulation order
df = df.sort_values(['SystemCodeNumber', 'Timestamp']).reset_index(drop=True)

# Track current price per parking lot
latest_price = {lot: BASE_PRICE for lot in df['SystemCodeNumber'].unique()}

# Stream simulation: process each row one by one
for idx, row in df.iterrows():
    lot = row['SystemCodeNumber']
    occ_rate = row['Occupancy'] / row['Capacity']
    
    # Compute updated price
    new_price = latest_price[lot] + ALPHA * occ_rate
    new_price = max(5, min(new_price, 30))  # Bound price

    latest_price[lot] = new_price

    # Add new row to results with updated price
    row_dict = row.to_dict()
    row_dict['Price'] = new_price
    streamed_rows.append(row_dict)

# Convert final list back to DataFrame
df_stream = pd.DataFrame(streamed_rows)

# Preview first few simulated streaming results
df_stream[['SystemCodeNumber', 'Timestamp', 'Occupancy', 'Capacity', 'Price']].head(20)

SystemCodeNumber           Timestamp  Occupancy  Capacity      Price
0       BHMBCCMKT01 2016-10-04 07:59:00         61       577  10.528596
1       BHMBCCMKT01 2016-10-04 08:25:00         64       577  11.083189
2       BHMBCCMKT01 2016-10-04 08:59:00         80       577  11.776430
3       BHMBCCMKT01 2016-10-04 09:32:00        107       577  12.703640
4       BHMBCCMKT01 2016-10-04 09:59:00        150       577  14.003466
5       BHMBCCMKT01 2016-10-04 10:26:00        177       577  15.537262
6       BHMBCCMKT01 2016-10-04 10:59:00        219       577  17.435009
7       BHMBCCMKT01 2016-10-04 11:25:00        247       577  19.575390
8       BHMBCCMKT01 2016-10-04 11:59:00        259       577  21.819757
9       BHMBCCMKT01 2016-10-04 12:29:00        266       577  24.124783
10      BHMBCCMKT01 2016-10-04 13:02:00        269       577  26.455806
11      BHMBCCMKT01 2016-10-04 13:29:00        263       577  28.734835
12      BHMBCCMKT01 2016-10-04 14:02:00        238       577  30.000000
13      BHMBCCMKT01 2016-10-04 14:29:00        215       577  30.000000
14      BHMBCCMKT01 2016-10-04 14:57:00        192       577  30.000000
15      BHMBCCMKT01 2016-10-04 15:30:00        165       577  30.000000
16      BHMBCCMKT01 2016-10-04 16:04:00        162       577  30.000000
17      BHMBCCMKT01 2016-10-04 16:31:00        143       577  30.000000
18      BHMBCCMKT01 2016-10-05 07:57:00         54       577  30.000000
19      BHMBCCMKT01 2016-10-05 08:30:00         59       577  30.000000

## ✅ **Step 7: Live Visualization Using Bokeh**

In [79]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource
from bokeh.palettes import Category10
from bokeh.layouts import layout

In [80]:
output_notebook()

# Simulate or use your actual df from pricing steps
# Assuming df contains columns: SystemCodeNumber, Timestamp, Price
df['Timestamp'] = pd.to_datetime(df['Timestamp'])  # Ensure proper datetime

Loading BokehJS ...

In [81]:
# Create figure for time series price visualization
p = figure(
    x_axis_type='datetime',
    title='Dynamic Pricing Over Time',
    height=400,
    width=800
)

p.line(df['Timestamp'], df['Price'], line_width=2, color='crimson', legend_label='Price')

p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price ($)'
p.legend.location = 'top_left'

show(p)

1. Multi-line visualization: Track pricing for several parking lots in real time

In [82]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import Viridis256
import pandas as pd

output_notebook()

df['Timestamp'] = pd.to_datetime(df['Timestamp'])

# Group by parking lot
lots = df['SystemCodeNumber'].unique()

p = figure(
    x_axis_type='datetime',
    title='Pricing Over Time for Multiple Parking Lots',
    width=800,
    height=400
)
p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price ($)'

# Use Viridis256 for more color variety
palette = Viridis256
for i, lot in enumerate(lots):
    lot_data = df[df['SystemCodeNumber'] == lot]
    source = ColumnDataSource(lot_data)
    color = palette[int(i * (255 / max(1, len(lots)-1)))]
    p.line('Timestamp', 'Price', source=source, color=color, legend_label=f'Lot {lot}', line_width=2)
    p.scatter('Timestamp', 'Price', source=source, color=color, size=5, marker='circle')

p.legend.location = "top_left"
p.legend.click_policy = "hide"  

# Add hover tool
tooltips = [
    ('Lot', '@SystemCodeNumber'),
    ('Time', '@Timestamp{%F %T}'),
    ('Price', '@Price{$0.00}')
]
hover = HoverTool(tooltips=tooltips, formatters={'@Timestamp': 'datetime'}, mode='vline')
p.add_tools(hover)

show(p)

Loading BokehJS ...

2. Visualizing Your Prices Versus Competitors Over Time

In [83]:
competitor_data = []

for lot in df['SystemCodeNumber'].unique():
    lot_data = df[df['SystemCodeNumber'] == lot]
    n = len(lot_data)
    competitor_prices = np.random.uniform(8, 25, n)
    competitor_data.append(
        pd.DataFrame({
            'SystemCodeNumber': lot,
            'Timestamp': lot_data['Timestamp'].values,
            'CompetitorPrice': competitor_prices
        })
    )

df_competitor = pd.concat(competitor_data, ignore_index=True)

In [84]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import Plasma256

# Assuming 'lots', 'df', and 'df_competitor' are already defined in your code

p = figure(
    x_axis_type='datetime',
    title='Your Price vs Competitor Price Over Time',
    width=800,
    height=400
)

# Use Plasma256 for distinct lines
palette = Plasma256

for i, lot in enumerate(lots):
    lot_data = df[df['SystemCodeNumber'] == lot]
    competitor_data = df_competitor[df_competitor['SystemCodeNumber'] == lot]
    
    source_your = ColumnDataSource(lot_data)
    source_comp = ColumnDataSource(competitor_data)
    
    color = palette[int(i * (255 / max(1, len(lots)-1)))]
    
    p.line('Timestamp', 'Price', source=source_your, color=color, legend_label=f'Your Lot {lot}', line_width=2)
    p.line('Timestamp', 'CompetitorPrice', source=source_comp, color=color, line_dash='dashed', legend_label=f'Competitor Lot {lot}', line_width=2)

p.legend.location = "top_left"
p.legend.click_policy = "hide"

hover = HoverTool(tooltips=[
    ('Lot', '@SystemCodeNumber'),
    ('Time', '@Timestamp{%F %T}'),
    ('Price', '$@Price{0.00}'),
    ('Competitor Price', '$@CompetitorPrice{0.00}')
], formatters={'@Timestamp': 'datetime'}, mode='vline')

p.add_tools(hover)

show(p)